In [1]:
import numpy as np
import configur
import pandas as pd
import yfinance as yf
from datetime import datetime, timedelta
import time
import matplotlib.pyplot as plt
import math
import heapq
import random
from openpyxl import load_workbook
import os

In [2]:
# Initializes booleans (check these, they could be important)
tradeable = False

# Empty Initializations
profits = []
ticker_list = []
tickers = []
symbols = []

profit = 0

new = [()]


In [3]:
# This is currently a manual merge of the optimal stock lists, will automante soon
big=[]
small = []
dupes=[]
# fiveyear=some list of tickers from StockFinder.ipynb
# oneyear=some list of tickers from StockFinder.ipynb
# twoyear=some list of tickers from StockFinder.ipynb

dupes = fiveyear + twoyear + oneyear


# Convert final list to set() and then set to list() to remove duplicates for a big list
big = list(set(dupes))
print(len(big))
# Uses set to get all possible overlaps for a smaller list
small= list(set(fiveyear) & set(twoyear))+list(set(fiveyear) & set(oneyear))+list(set(twoyear) & set(oneyear))
print(len(small))
# ticker_list = some list of tickersfrom StockFinder.ipynb
ticker_list = ['NEW','JOB','CEI','NAK','TLOFF','VTGDF','SSFT']

520
67


In [4]:
 # Smoothing with Wilder puts emphasis on recent values
def Wilder(data, periods):
    start = np.where(~np.isnan(data))[0][0] # Check if nans present in beginning
    Wilder = np.array([np.nan]*len(data))
    Wilder[start+periods-1] = data[start:(start+periods)].mean() # Simple Moving Average
    for i in range(start+periods,len(data)):
        Wilder[i] = (Wilder[i-1]*(periods-1) + data[i])/periods # Wilder Smoothing
    return(Wilder)

In [5]:
def update():
    global profits    
    global profit
    global ticker_list
    global new
    global tickers
    global tradeable

    for t in ticker_list:
        if type(t) is list:
            t = t[0]
        try:
            tradeable = False
            
            # Gets data for backtesting
            df = yf.download(tickers=t, period = '1y', interval = '1d')
            df.drop(['Close'], axis=1, inplace=True)
            df['Close'] = df['Adj Close']
            close = df.iloc[-1, df.columns.get_loc('Adj Close')]

            tradeable = True
            biglist = []
            
            if (tradeable):
                df['symbol'] = str(t).upper()
                shortEMA = 5
                # While loops are set up to iterate over each possible paramater in a range
                # i.e. (5 25 5 6, 5 25 5 7, 5 25 5 8, 5 25 6 6, etc.. all the way to 10 40 12 8)
                while (shortEMA <= 12):
                    # # Looping this every so often to form live update on bigger trends
                    # First find the MACD and check if it is higher than the signal (bullish)
                    longEMA = 25
                    signal = 5
                    rviRange = 6
                    while (longEMA <= 41):
                        signal = 5
                        rviRange = 6
                        if (longEMA >= 41):
                            shortEMA += 1
                        while (signal <= 11):
                            rviRange = 6
                            if (signal >= 11):
                                longEMA += 1
                            while (rviRange <= 14):
                                # No overlap: Only runs if this is the first time trying this combo for this stock
                                if ((str(shortEMA) +' '+ str(longEMA)  +' '+ str(signal)  +' '+ str(rviRange)) not in biglist):
                                    biglist.append((str(shortEMA) +' '+ str(longEMA)  +' '+ str(signal)  +' '+ str(rviRange)))
                                    parameters = []     # This list gets reset every parameter; biglist gets reset every stock
                                    parameters.append((str(shortEMA) +' '+ str(longEMA)  +' '+ str(signal)  +' '+ str(rviRange)))
                                    
                                    # Shifts in MACD and RVI are used to determine signal direction and strength -- we are optimizing their parameters
                                    df['ShortEMA'] = df.Close.transform(lambda x: x.ewm(span=shortEMA, adjust=False).mean())
                                    df['LongEMA'] = df.Close.transform(lambda x: x.ewm(span=longEMA, adjust=False).mean())
                                    df['MACD'] = df.ShortEMA - df.LongEMA
                                    df['signal'] = df.MACD.transform(lambda x: x.ewm(span=signal, adjust=False).mean())
                                    if (rviRange >= 14):
                                        signal += 1
                                        
                                    # All the necessary calculations for the RVI, including the RVI Signal, including the optimization
                                    df['open_shift'] = df.Open.shift(1)
                                    df['open_shift2'] = df.Open.shift(2)
                                    df['open_shift3'] = df.Open.shift(3)
                                    df['low_shift'] = df.Low.shift(1)
                                    df['low_shift2'] = df.Low.shift(2)
                                    df['low_shift3'] = df.Low.shift(3)
                                    df['numerator'] = ((1 * (df.Close - df.Open)) + (2 * (df.Close - df.open_shift)) + (2 * (df.Close - df.open_shift2)) + 
                                                       (1 * (df.Close - df.open_shift3))) / 6
                                    df['denominator'] = (1 * (df.High - df.Low) + (2 * (df.High - df.low_shift)) + (2 * (df.High - df.low_shift2)) + 
                                                       (1 * (df.High - df.low_shift3))) / 6
                                    df['SMA_numerator'] = df['numerator'].transform(lambda x: x.rolling(window = rviRange).mean())
                                    df['SMA_denominator'] = df['denominator'].transform(lambda x: x.rolling(window = rviRange).mean())   
                                    rviRange += 1 # Optimizing Parameters for RVI
                        
                                    df['RVI'] = df['SMA_numerator'] / df['SMA_denominator']          
                                    df['rvishift'] = df.RVI.shift(1)
                                    df['rvishift2'] = df.RVI.shift(2)
                                    df['rvishift3'] = df.RVI.shift(3)
                                    df['RVI_Signal'] = ((1* df.RVI) + (2 * df.rvishift) + (2 * df.rvishift2) + (1*df.rvishift3)) / 6

                                    # ATR ratio and ADX is used to figure out a true range, for volatility and signal strength
                                    df['prev_close'] = df.groupby('symbol')['Close'].shift(1)
                                    df['TR'] = np.maximum((df['High'] - df['Low']), 
                                                        np.maximum(abs(df['High'] - df['prev_close']), 
                                                        abs(df['prev_close'] - df['Low'])))

                                    for i in df['symbol'].unique():
                                        TR_data = df[df.symbol == i].copy()
                                        df.loc[df.symbol==i,'ATR_5'] = Wilder(TR_data['TR'], 5)
                                        df.loc[df.symbol==i,'ATR_15'] = Wilder(TR_data['TR'], 15)
                                    df['ATR_Ratio'] = df['ATR_5'] / df['ATR_15']

                                    df['prev_high'] = df.groupby('symbol')['High'].shift(1)
                                    df['prev_low'] = df.groupby('symbol')['Low'].shift(1)
                                    df['+DM'] = np.where(~np.isnan(df.prev_high),
                                                            np.where((df['High'] > df['prev_high']) & 
                                            (((df['High'] - df['prev_high']) > (df['prev_low'] - df['Low']))), 
                                                                                                    df['High'] - df['prev_high'], 
                                                                                                    0),np.nan)
                                    df['-DM'] = np.where(~np.isnan(df.prev_low),
                                                            np.where((df['prev_low'] > df['Low']) & 
                                            (((df['prev_low'] - df['Low']) > (df['High'] - df['prev_high']))), 
                                                                        df['prev_low'] - df['Low'], 
                                                                        0),np.nan)
                                    for i in df['symbol'].unique():
                                        ADX_data = df[df.symbol == i].copy()
                                        df.loc[df.symbol==i,'+DM_15'] = Wilder(ADX_data['+DM'], 15)
                                        df.loc[df.symbol==i,'-DM_15'] = Wilder(ADX_data['-DM'], 15)
                                    df['+DI_15'] = (df['+DM_15']/df['ATR_15'])*100
                                    df['-DI_15'] = (df['-DM_15']/df['ATR_15'])*100
                                    df['DX_15'] = (np.round(abs(df['+DI_15'] - df['-DI_15'])/(df['+DI_15'] + df['-DI_15']) * 100))
                                    for i in df['symbol'].unique():
                                        ADX_data = df[df.symbol == i].copy()
                                        df.loc[df.symbol==i,'ADX_15'] = Wilder(ADX_data['DX_15'], 15)
                                    
                                     # Here is where the main bullish/bearish signal columns are determined as either 0 or 1 based on the inline if conditions
                                    # The goal is to build a strategy from these signals
                                    df['rvi_bullish'] = df.apply(lambda x : 1 if (x['RVI'] - x['RVI_Signal'] > 0) else 0, axis = 1)
                                    df['macd_bullish'] = df.apply(lambda x : 1 if (x['MACD'] - x['signal'] > 0) else 0, axis = 1)
                                    df['adx_signal'] = df.apply(lambda x : 1 if (x['ADX_15'] >= 25) else 0, axis = 1)
                                    df['atr_signal'] = df.apply(lambda x : 1 if (x['ATR_Ratio'] >= 1) else 0, axis = 1)
                                        
                                    df['in_position_shifted'] = 3
                                    tickers.append(t)
                                
                                    # CURRENT STRATEGY (OPTIMIZED PARAMETER STORAGE)
                                    # Bullish when [(MACD or RVI) and (ADX or ATR) bullish] or [(MACD and RVI) bullish]
                                    df['in_position'] = df.apply(lambda x : 1 if ((x.macd_bullish + x.rvi_bullish >= 1 and x.adx_signal + x.atr_signal >= 1) or (x.macd_bullish + x.rvi_bullish == 2)) else 0, axis = 1)
                                    # Bearish when [(MACD and RVI) bearish] or [(MACD and (ADX or ATR)) bearish]
                                    df['in_position'] = df.apply(lambda x : (0) if (x.macd_bullish == 0 and x.adx_signal + x.atr_signal > 1) else x['in_position'], axis = 1)

                                    flag = False
                                    while (flag==False):    # Iterates through past data; stops when loop is not causing any changes to df
                                        copy = df.copy()
                                        # Checks if it was in position yesterday
                                        df['in_position_shifted'] = df['in_position'].shift(1)
                                        # If [MACD or RVI bullish] and [it was in position yesterday], stays in position 
                                        df['in_position'] = df.apply(lambda x : (1) if ((x.macd_bullish + x.rvi_bullish >= 1) or (x.adx_signal + x.atr_signal == 2 and x.macd_bullish + x.rvi_bullish >= 1)) and (x.in_position_shifted == 1) else x['in_position'], axis = 1)
                                        flag = ((df.in_position == copy.in_position).all())
                                      

                                    # Initializes empty lists and [bought, sold] columns
                                    i = 0
                                    df['bought'] = 0
                                    df['sold'] = 0
                                    bought,sold,profits,profitable_trades,nonprofitable_trades,profitable_trade_ratios = ([] for i in range(6))
                                    average_returns,without_bests,percentages,wouldve,trade_counts,in_positions = ([] for i in range(6))
                              
                                    # Gets prices that were bought and sold at, and calculates profit
                                    while (i < len(df)):
                                        # If it is in position now, but wasnt in one day ago --> buys at close
                                        if (df.iloc[i, df.columns.get_loc('in_position')] == 1):
                                            if (df.iloc[i, df.columns.get_loc('in_position_shifted')] == 0):
                                                df.iloc[i, df.columns.get_loc('bought')] = df.iloc[i, df.columns.get_loc('Close')]
                                                bought.append(df.iloc[i, df.columns.get_loc('Close')])
                                            if (len(bought) > 0):
                                                # Checks if this individual trade is profitable so far
                                                if (close / bought[-1] > 1 and i == len(df) - 1): 
                                                    profitable_trades.append(((close / bought[-1]) - 1 )* 100)
                                                elif (close / bought[-1] < 1 and i == len(df) - 1):
                                                    nonprofitable_trades.append(((close / bought[-1]) - 1 )* 100)
                                        # If it was in position but is not anymore --> sold at close
                                        if (df.iloc[i, df.columns.get_loc('in_position')] == 0 and df.iloc[i, df.columns.get_loc('in_position_shifted')] == 1):
                                            df.iloc[i, df.columns.get_loc('sold')] = df.iloc[i, df.columns.get_loc('Close')]
                                            sold.append(df.iloc[i, df.columns.get_loc('Close')])
                                            profits.append(sold[-1] - bought[-1])
                                            # Checks if this individual trade was profitable and adds it to lists
                                            if (sold[-1] / bought[-1] >= 1): 
                                                profitable_trades.append(((sold[-1] / bought[-1]) - 1) * 100)
                                            else:
                                                nonprofitable_trades.append(((sold[-1] / bought[-1]) - 1) * 100)   
                                        i += 1

                                    # Calculates profit and handles case where in_position is true
                                    df.index = df.index.tz_localize(None)
                                    df['Profit'] = df.sold.sum() - df.bought.sum()
                                    if df.iloc[-1, df.columns.get_loc('in_position')] == 1:
                                        df['Profit'] += close

                                    # Percentage of "buy and hold" strategy VS percentage gains of this strategy
                                    perc = (((df['Profit'][0] + bought[0]) / bought[0]) -1) * 100
                                    wouldveperc = ((close / bought[0]) * 100) - 100
                                    percentages.append('{0:.2f}'.format(perc) + "%") # % would have made if had followed the strat
                                    wouldve.append('{0:.2f}'.format(wouldveperc) + "%") # % wouldve made from buying and holding
                                    trade_counts.append(len(profitable_trades) + len(nonprofitable_trades))

                                    # Checks ratio of profitable to non-profitable trades and average % per trade
                                    profitable_trade_ratio = len(profitable_trades) / (len(nonprofitable_trades) + len(profitable_trades))
                                    average_return = (sum(profitable_trades) + sum(nonprofitable_trades)) / (len(profitable_trades) + len(nonprofitable_trades))
                                    # Removes the 2 best trades (outliers) and calculates average return
                                    without_best = (sum(profitable_trades) - max(profitable_trades) - heapq.nlargest(2, profitable_trades)[1] + sum(nonprofitable_trades)) / (len(profitable_trades) + len(nonprofitable_trades) - 2)

                                    profitable_trade_ratios.append('{0:.5f}'.format(profitable_trade_ratio))
                                    average_returns.append('{0:.5f}'.format(average_return))
                                    without_bests.append('{0:.5f}'.format(without_best))
                                    in_positions.append(df.iloc[-1, df.columns.get_loc('bought')])

                                    # Realignment -- fixes any potential issues through splicing
                                    while (len(tickers) != len(profitable_trade_ratios)):
                                        tickers = tickers[:-2] + tickers[-1:]
                                        percentages = percentages[:-2] + percentages[-1:]
                                        wouldve = wouldve[:-2] + wouldve[-1:]
                                    while (len(trade_counts) != len(profitable_trade_ratios)):
                                        trade_counts = trade_counts[:-2] + trade_counts[-1:]

                                    new.extend(zip(tickers,parameters,percentages,wouldve,profitable_trade_ratios,average_returns,without_bests,trade_counts,in_positions))
                                    print (new[-1])

                                    if (str(t) == str(ticker_list[-1]) and len(ticker_list) > 5):
                                        print(new)

                                # Here we handle the logic for looping through the roughly 10,000 parameter combinations
                                else: 
                                    if (longEMA >= 41):
                                        shortEMA+=1
                                        signal = 5
                                        rviRange = 6
                                        longEMA = 25
                                        if (signal >= 11):
                                            longEMA+=1
                                            shortEMA = 5
                                            signal = 5
                                            rviRange = 6
                                            if (rviRange >= 14):
                                                longEMA=25
                                                shortEMA = 5
                                                rviRange = 6
                                                signal+=1
                                                
                                    elif (signal >= 11):
                                        longEMA+=1
                                        shortEMA = 5
                                        signal = 5
                                        rviRange = 6
                                        if (rviRange >= 14):
                                            longEMA=25
                                            shortEMA = 5
                                            rviRange = 6
                                            signal+=1
                                            
                                    elif (rviRange >= 14):
                                        longEMA=25
                                        shortEMA = 5
                                        rviRange = 6
                                        signal+=1
        except Exception as e:
            print (e)

In [6]:
update()


[*********************100%***********************]  1 of 1 completed
('NEW', '5 25 5 6', '2.41%', '-96.59%', '0.26415', '0.26710', '-3.02195', 53, 0.0)
('NEW', '5 25 5 7', '-5.05%', '-96.59%', '0.27451', '0.07981', '-3.35113', 51, 0.0)
('NEW', '5 25 5 8', '-37.23%', '-96.59%', '0.25455', '-1.22846', '-4.42975', 55, 0.0)
('NEW', '5 25 5 9', '-32.42%', '-96.59%', '0.26923', '-1.24240', '-4.63633', 52, 0.0)
('NEW', '5 25 5 10', '-8.59%', '-96.59%', '0.27660', '-0.89803', '-4.26205', 47, 0.0)
('NEW', '5 25 5 11', '-21.69%', '-96.59%', '0.30612', '-1.42508', '-4.66839', 49, 0.0)
('NEW', '5 25 5 12', '-12.55%', '-96.59%', '0.28000', '-1.23895', '-4.52451', 50, 0.0)
('NEW', '5 25 5 13', '-10.36%', '-96.59%', '0.26531', '-1.24768', '-4.44591', 49, 0.0)
('NEW', '5 25 5 14', '-10.21%', '-96.59%', '0.26000', '-1.18384', '-4.31278', 50, 0.0)
('NEW', '5 25 6 6', '-18.36%', '-96.59%', '0.30000', '-0.27190', '-3.35659', 50, 0.0)
('NEW', '5 25 6 7', '-20.19%', '-96.59%', '0.30000', '-0.45263', '-3.544

('NEW', '5 26 8 10', '-33.64%', '-96.59%', '0.25581', '-2.07174', '-4.41858', 43, 0.0)
('NEW', '5 26 8 11', '-46.04%', '-96.59%', '0.30435', '-2.41047', '-4.61269', 46, 0.0)
('NEW', '5 26 8 12', '-29.74%', '-96.59%', '0.28261', '-1.63898', '-3.99038', 46, 0.0)
('NEW', '5 26 8 13', '-34.53%', '-96.59%', '0.24444', '-2.15272', '-4.46646', 45, 0.0)
('NEW', '5 26 8 14', '-47.17%', '-96.59%', '0.26531', '-2.68320', '-4.82260', 49, 0.0)
('NEW', '5 26 9 6', '-30.65%', '-96.59%', '0.28000', '-0.98807', '-3.45146', 50, 0.0)
('NEW', '5 26 9 7', '-32.33%', '-96.59%', '0.28000', '-1.15208', '-3.62230', 50, 0.0)
('NEW', '5 26 9 8', '-41.87%', '-96.59%', '0.27451', '-1.98006', '-4.41439', 51, 0.0)
('NEW', '5 26 9 9', '-32.60%', '-96.59%', '0.23913', '-1.83229', '-4.53654', 46, 0.0)
('NEW', '5 26 9 10', '-33.88%', '-96.59%', '0.25581', '-2.01970', '-4.54148', 43, 0.0)
('NEW', '5 26 9 11', '-44.21%', '-96.59%', '0.28889', '-2.46702', '-4.89231', 45, 0.0)
('NEW', '5 26 9 12', '-24.60%', '-96.59%', '0.2

('NEW', '5 28 5 6', '2.91%', '-96.59%', '0.27451', '0.27533', '-3.14763', 51, 0.0)
('NEW', '5 28 5 7', '-5.94%', '-96.59%', '0.28000', '0.01147', '-3.49379', 50, 0.0)
('NEW', '5 28 5 8', '-35.16%', '-96.59%', '0.26415', '-1.21158', '-4.53776', 53, 0.0)
('NEW', '5 28 5 9', '-29.65%', '-96.59%', '0.27451', '-1.20518', '-4.66686', 51, 0.0)
('NEW', '5 28 5 10', '-6.22%', '-96.59%', '0.28261', '-0.77957', '-4.21467', 46, 0.0)
('NEW', '5 28 5 11', '-21.20%', '-96.59%', '0.30000', '-1.37850', '-4.55230', 50, 0.0)
('NEW', '5 28 5 12', '-13.09%', '-96.59%', '0.27451', '-1.26904', '-4.48878', 51, 0.0)
('NEW', '5 28 5 13', '-12.83%', '-96.59%', '0.24000', '-1.40231', '-4.54035', 50, 0.0)
('NEW', '5 28 5 14', '-13.67%', '-96.59%', '0.26000', '-1.39338', '-4.53105', 50, 0.0)
('NEW', '5 28 6 6', '-13.71%', '-96.59%', '0.26923', '-0.03752', '-2.98944', 52, 0.0)
('NEW', '5 28 6 7', '-23.60%', '-96.59%', '0.28000', '-0.33439', '-3.42168', 50, 0.0)
('NEW', '5 28 6 8', '-38.58%', '-96.59%', '0.26923', '-

('NEW', '5 29 8 11', '-43.22%', '-96.59%', '0.28889', '-2.37391', '-4.79487', 45, 0.0)
('NEW', '5 29 8 12', '-23.62%', '-96.59%', '0.27907', '-1.45664', '-3.88217', 43, 0.0)
('NEW', '5 29 8 13', '-26.82%', '-96.59%', '0.23256', '-1.86015', '-4.33599', 43, 0.0)
('NEW', '5 29 8 14', '-39.32%', '-96.59%', '0.27083', '-2.23895', '-4.57048', 48, 0.0)
('NEW', '5 29 9 6', '-27.84%', '-96.59%', '0.26531', '-0.67788', '-3.37836', 49, 0.0)
('NEW', '5 29 9 7', '-29.02%', '-96.59%', '0.26531', '-0.80522', '-3.51112', 49, 0.0)
('NEW', '5 29 9 8', '-38.64%', '-96.59%', '0.26000', '-1.68001', '-4.34632', 50, 0.0)
('NEW', '5 29 9 9', '-29.67%', '-96.59%', '0.23913', '-1.52720', '-4.42895', 46, 0.0)
('NEW', '5 29 9 10', '-32.20%', '-96.59%', '0.23810', '-1.84536', '-4.80495', 42, 0.0)
('NEW', '5 29 9 11', '-41.25%', '-96.59%', '0.27907', '-2.29423', '-5.11558', 43, 0.0)
('NEW', '5 29 9 12', '-21.64%', '-96.59%', '0.26829', '-1.32173', '-4.21829', 41, 0.0)
('NEW', '5 29 9 13', '-23.36%', '-96.59%', '0.2

('NEW', '5 31 5 7', '-11.87%', '-96.59%', '0.26923', '0.22518', '-3.13133', 52, 0.0)
('NEW', '5 31 5 8', '-26.75%', '-96.59%', '0.25926', '-0.64208', '-3.88238', 54, 0.0)
('NEW', '5 31 5 9', '-21.79%', '-96.59%', '0.27451', '-0.66473', '-4.10434', 51, 0.0)
('NEW', '5 31 5 10', '-10.02%', '-96.59%', '0.27660', '-0.35309', '-3.69290', 47, 0.0)
('NEW', '5 31 5 11', '-25.10%', '-96.59%', '0.28571', '-1.26751', '-4.50411', 49, 0.0)
('NEW', '5 31 5 12', '-16.80%', '-96.59%', '0.28000', '-1.15010', '-4.43196', 50, 0.0)
('NEW', '5 31 5 13', '-14.86%', '-96.59%', '0.24000', '-1.21484', '-4.34508', 50, 0.0)
('NEW', '5 31 5 14', '-16.48%', '-96.59%', '0.25490', '-1.24149', '-4.30893', 51, 0.0)
('NEW', '5 31 6 6', '-20.53%', '-96.59%', '0.25926', '-0.40896', '-3.26163', 54, 0.0)
('NEW', '5 31 6 7', '-31.46%', '-96.59%', '0.26923', '-0.73133', '-3.71101', 52, 0.0)
('NEW', '5 31 6 8', '-42.28%', '-96.59%', '0.25926', '-1.49876', '-4.37519', 54, 0.0)
('NEW', '5 31 6 9', '-31.18%', '-96.59%', '0.26531

...

('VTGDF', '12 37 11 9', '-963.33%', '-50.00%', '0.15294', '-13.60328', '-15.75120', 85, 0.0)
('VTGDF', '12 37 11 10', '-964.17%', '-50.00%', '0.15294', '-13.44777', '-15.38541', 85, 0.0)
('VTGDF', '12 37 11 11', '-1104.17%', '-50.00%', '0.15294', '-14.50771', '-16.40204', 85, 0.0)
('VTGDF', '12 37 11 12', '-1060.00%', '-50.00%', '0.12500', '-13.41423', '-15.33010', 88, 0.0)
('VTGDF', '12 37 11 13', '-1065.55%', '-49.58%', '0.17778', '-13.41709', '-15.17900', 90, 0.0)
('VTGDF', '12 37 11 14', '-1051.67%', '-50.00%', '0.13636', '-13.63573', '-15.35278', 88, 0.0)
('VTGDF', '12 37 5 6', '-1029.41%', '-49.58%', '0.15888', '-11.86186', '-13.69237', 107, 0.0)
('VTGDF', '12 37 5 7', '-937.82%', '-49.58%', '0.17143', '-11.47562', '-13.24491', 105, 0.0)
('VTGDF', '12 37 5 8', '-1044.54%', '-49.58%', '0.17273', '-12.14960', '-13.87592', 110, 0.0)
('VTGDF', '12 37 5 9', '-1055.46%', '-49.58%', '0.15686', '-13.35637', '-15.24492', 102, 0.0)
('VTGDF', '12 37 5 10', '-1169.75%', '-49.58%', '0.13208',

('VTGDF', '12 38 7 7', '-764.71%', '-49.58%', '0.20000', '-9.76752', '-11.67276', 95, 0.0)
('VTGDF', '12 38 7 8', '-845.38%', '-49.58%', '0.20213', '-11.44552', '-13.40795', 94, 0.0)
('VTGDF', '12 38 7 9', '-920.83%', '-50.00%', '0.16484', '-12.91259', '-15.10484', 91, 0.0)
('VTGDF', '12 38 7 10', '-977.50%', '-50.00%', '0.16129', '-13.18523', '-15.33530', 93, 0.0)
('VTGDF', '12 38 7 11', '-1001.67%', '-50.00%', '0.17391', '-13.26249', '-15.43817', 92, 0.0)
('VTGDF', '12 38 7 12', '-967.50%', '-50.00%', '0.13684', '-12.12361', '-14.29422', 95, 0.0)
('VTGDF', '12 38 7 13', '-914.29%', '-49.58%', '0.18280', '-11.82967', '-13.94994', 93, 0.0)
('VTGDF', '12 38 7 14', '-922.50%', '-50.00%', '0.13978', '-11.84800', '-13.96868', 93, 0.0)
('VTGDF', '12 38 8 6', '-769.75%', '-49.58%', '0.17582', '-9.92234', '-11.91668', 91, 0.0)
('VTGDF', '12 38 8 7', '-736.13%', '-49.58%', '0.18280', '-9.60820', '-11.55181', 93, 0.0)
('VTGDF', '12 38 8 8', '-841.18%', '-49.58%', '0.19355', '-11.63159', '-13.61

('VTGDF', '12 39 9 14', '-975.83%', '-50.00%', '0.14130', '-12.47879', '-14.49816', 92, 0.0)
('VTGDF', '12 39 10 6', '-961.34%', '-49.58%', '0.16304', '-11.81784', '-13.45591', 92, 0.0)
('VTGDF', '12 39 10 7', '-884.03%', '-49.58%', '0.17021', '-10.93081', '-12.47707', 94, 0.0)
('VTGDF', '12 39 10 8', '-1006.72%', '-49.58%', '0.19355', '-13.10249', '-14.71347', 93, 0.0)
('VTGDF', '12 39 10 9', '-954.17%', '-50.00%', '0.17442', '-13.62903', '-15.38680', 86, 0.0)
('VTGDF', '12 39 10 10', '-967.50%', '-50.00%', '0.13953', '-13.64456', '-15.40270', 86, 0.0)
('VTGDF', '12 39 10 11', '-1090.83%', '-50.00%', '0.15294', '-14.62811', '-16.43113', 85, 0.0)
('VTGDF', '12 39 10 12', '-1030.83%', '-50.00%', '0.12500', '-13.36380', '-15.24112', 88, 0.0)
('VTGDF', '12 39 10 13', '-1052.10%', '-49.58%', '0.16854', '-13.62269', '-15.31971', 89, 0.0)
('VTGDF', '12 39 10 14', '-1041.67%', '-50.00%', '0.13333', '-13.37517', '-15.04727', 90, 0.0)
('VTGDF', '12 40 11 6', '-964.71%', '-49.58%', '0.15385', '-

('VTGDF', '13 41 5 12', '-1213.45%', '-49.58%', '0.11215', '-13.87095', '-15.77461', 107, 0.0)
('VTGDF', '13 41 5 13', '-1086.55%', '-49.58%', '0.15385', '-12.79019', '-14.70064', 104, 0.0)
('VTGDF', '13 41 5 14', '-1116.81%', '-49.58%', '0.11650', '-13.12118', '-15.05710', 103, 0.0)
('VTGDF', '13 41 6 6', '-890.76%', '-49.58%', '0.18000', '-10.61070', '-12.45261', 100, 0.0)
('VTGDF', '13 41 6 7', '-816.81%', '-49.58%', '0.19192', '-10.19785', '-12.05023', 99, 0.0)
('VTGDF', '13 41 6 8', '-935.29%', '-49.58%', '0.19000', '-11.95901', '-13.82844', 100, 0.0)
('VTGDF', '13 41 6 9', '-972.27%', '-49.58%', '0.16842', '-12.98226', '-15.08173', 95, 0.0)
('VTGDF', '13 41 6 10', '-1008.40%', '-49.58%', '0.15464', '-13.24205', '-15.30279', 97, 0.0)
('VTGDF', '13 41 6 11', '-1100.00%', '-49.58%', '0.16495', '-13.74167', '-15.81292', 97, 0.0)
('VTGDF', '13 41 6 12', '-1045.38%', '-49.58%', '0.14141', '-12.56352', '-14.56777', 99, 0.0)
('VTGDF', '13 41 6 13', '-987.39%', '-49.58%', '0.16495', '-12.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [7]:
df = pd.DataFrame(new, columns =['Ticker', 'Parameters','Profit (in %)', 'Wouldve Made (in %)', 'Profitable Trade Ratio', 'Avg Return', 'Avg Without Best', '# of Trades','Bought Price'])
df

Ticker   Parameters Profit (in %) Wouldve Made (in %)  \
0       None         None          None                None   
1        NEW     5 25 5 6         2.41%             -96.59%   
2        NEW     5 25 5 7        -5.05%             -96.59%   
3        NEW     5 25 5 8       -37.23%             -96.59%   
4        NEW     5 25 5 9       -32.42%             -96.59%   
...      ...          ...           ...                 ...   
59972   SSFT  13 42 11 10       -14.97%             118.35%   
59973   SSFT  13 42 11 11      -143.22%              50.00%   
59974   SSFT  13 42 11 12        82.33%              50.00%   
59975   SSFT  13 42 11 13         7.94%              52.62%   
59976   SSFT  13 42 11 14       214.24%              52.62%   

      Profitable Trade Ratio Avg Return Avg Without Best  # of Trades  \
0                       None       None             None          NaN   
1                    0.26415    0.26710         -3.02195         53.0   
2                    0.27451    0.07981         -3.35113         51.0   
3                    0.25455   -1.22846         -4.42975         55.0   
4                    0.26923   -1.24240         -4.63633         52.0   
...                      ...        ...              ...          ...   
59972                0.20588    9.91655         -3.62537         68.0   
59973                0.26087    8.53218         -4.77595         69.0   
59974                0.28788    9.91810         -2.71161         66.0   
59975                0.24615    8.02536         -4.86491         65.0   
59976                0.23438   10.33725         -4.06478         64.0   

       Bought Price  
0               NaN  
1               0.0  
2               0.0  
3               0.0  
4               0.0  
...             ...  
59972           0.0  
59973           0.0  
59974           0.0  
59975           0.0  
59976           0.0  

[59977 rows x 9 columns]

In [8]:
# Strip %, Fill na, set columns to numeric
df['Profit'] = df['Profit (in %)'].str.rstrip('%')
df['Wouldve Made'] = df['Wouldve Made (in %)'].str.rstrip('%')
df['Profit'] = df['Profit'].fillna(0)
df['Wouldve Made'] = df['Wouldve Made'].fillna(0)

df['Profit'] = pd.to_numeric(df['Profit'], errors='coerce')
df['Avg Without Best'] = pd.to_numeric(df['Avg Without Best'], errors='coerce')
df['Profitable Trade Ratio'] = pd.to_numeric(df['Profitable Trade Ratio'], errors='coerce')
df['Wouldve Made'] = pd.to_numeric(df['Wouldve Made'], errors='coerce')
df

Ticker   Parameters Profit (in %) Wouldve Made (in %)  \
0       None         None          None                None   
1        NEW     5 25 5 6         2.41%             -96.59%   
2        NEW     5 25 5 7        -5.05%             -96.59%   
3        NEW     5 25 5 8       -37.23%             -96.59%   
4        NEW     5 25 5 9       -32.42%             -96.59%   
...      ...          ...           ...                 ...   
59972   SSFT  13 42 11 10       -14.97%             118.35%   
59973   SSFT  13 42 11 11      -143.22%              50.00%   
59974   SSFT  13 42 11 12        82.33%              50.00%   
59975   SSFT  13 42 11 13         7.94%              52.62%   
59976   SSFT  13 42 11 14       214.24%              52.62%   

       Profitable Trade Ratio Avg Return  Avg Without Best  # of Trades  \
0                         NaN       None               NaN          NaN   
1                     0.26415    0.26710          -3.02195         53.0   
2                     0.27451    0.07981          -3.35113         51.0   
3                     0.25455   -1.22846          -4.42975         55.0   
4                     0.26923   -1.24240          -4.63633         52.0   
...                       ...        ...               ...          ...   
59972                 0.20588    9.91655          -3.62537         68.0   
59973                 0.26087    8.53218          -4.77595         69.0   
59974                 0.28788    9.91810          -2.71161         66.0   
59975                 0.24615    8.02536          -4.86491         65.0   
59976                 0.23438   10.33725          -4.06478         64.0   

       Bought Price  Profit  Wouldve Made  
0               NaN    0.00          0.00  
1               0.0    2.41        -96.59  
2               0.0   -5.05        -96.59  
3               0.0  -37.23        -96.59  
4               0.0  -32.42        -96.59  
...             ...     ...           ...  
59972           0.0  -14.97        118.35  
59973           0.0 -143.22         50.00  
59974           0.0   82.33         50.00  
59975           0.0    7.94         52.62  
59976           0.0  214.24         52.62  

[59977 rows x 11 columns]

In [9]:
# Outperform of our profit vs 'buy and hold' 
df['Outperform Ratio'] = df['Profit'] / df['Wouldve Made']

# Filters out any losing stocks, overall and on average per trade
filter = (df[["Profit", "Avg Without Best"]] > 0).all(axis=1)
df = df[filter]

# If wouldve made was negative, changes logic of Outperform Ratio, replace na
df['Outperform Ratio'] = df.apply(lambda x : (((-1 * x['Wouldve Made']) + x['Profit']) / (-1 * x['Wouldve Made'])) if (x['Wouldve Made'] < 0) else x['Outperform Ratio'], axis = 1)
df['Outperform Ratio'].replace([np.inf, -np.inf], np.nan, inplace=True)

df.head(5)

C:\Users\amoog\Anaconda3\envs\PythonData\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
C:\Users\amoog\Anaconda3\envs\PythonData\lib\site-packages\pandas\core\generic.py:6746: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)


Ticker Parameters Profit (in %) Wouldve Made (in %)  \
25706    NAK   5 25 5 7        29.63%             -50.62%   
25707    NAK   5 25 5 8        62.03%             -49.37%   
25708    NAK   5 25 5 9        40.79%             -47.37%   
25710    NAK  5 25 5 11        82.67%             -46.67%   
25711    NAK  5 25 5 12        52.11%             -43.66%   

       Profitable Trade Ratio Avg Return  Avg Without Best  # of Trades  \
25706                 0.47126    1.68158           0.39737         87.0   
25707                 0.43023    2.21924           0.58908         86.0   
25708                 0.46988    2.26487           0.65021         83.0   
25710                 0.46914    3.14321           1.50990         81.0   
25711                 0.46250    2.56039           1.21676         80.0   

       Bought Price  Profit  Wouldve Made  Outperform Ratio  
25706           0.0   29.63        -50.62          1.585342  
25707           0.0   62.03        -49.37          2.256431  
25708           0.0   40.79        -47.37          1.861094  
25710           0.0   82.67        -46.67          2.771373  
25711           0.0   52.11        -43.66          2.193541

In [10]:
# Filters low Outperform ratios, and low Profitable Trade Ratios
filter1 = (df[["Outperform Ratio"]] > 1).all(axis=1)
df = df[filter1]
filter2 = (df[["Profitable Trade Ratio"]] > .5).all(axis=1)
df = df[filter2]


In [11]:
# Breakdown: num trades: 30, avg w/o best: 25, profitable trade ratio: 25, outperform ratio: 20
a = (df['Outperform Ratio'])
q, bins = pd.qcut(a, 20, retbins=True, duplicates = 'drop')
print(bins)
bins = bins.tolist()
df['Outperform Bin Score'] = pd.cut(x=df['Outperform Ratio'], bins=bins, labels=False)
df['Outperform Bin Score'] = df['Outperform Bin Score'].fillna(0)
df['Outperform Bin Score'] = df.apply(lambda x : 20 if (x['Outperform Bin Score'] > 10) else x['Outperform Bin Score'], axis = 1)
df['Outperform Bin Score'] = df.apply(lambda x : 10 if (x['Outperform Bin Score'] > 6) else x['Outperform Bin Score'], axis = 1)

a = (df['# of Trades'])
q, bins = pd.qcut(a, 4, retbins=True, duplicates = 'drop')
print(bins)
bins = bins.tolist()
df['# Trades Bin Score'] = pd.cut(x=df['# of Trades'], bins=bins, labels=False)
df['# Trades Bin Score'] = df['# Trades Bin Score'].fillna(0)
df['# Trades Bin Score'] = (1+df['# Trades Bin Score'])*6

a = (df['Avg Without Best'])
q, bins = pd.qcut(a, 25, retbins=True, duplicates = 'drop')
print(bins)
bins = bins.tolist()
df['Avg w/o Best Bin Score'] = pd.cut(x=df['Avg Without Best'], bins=bins, labels=False)
df['Avg w/o Best Bin Score'] = df['Avg w/o Best Bin Score'].fillna(0)

a = (df['Profitable Trade Ratio'])
q, bins = pd.qcut(a, 25, retbins=True,duplicates = 'drop')
print(bins)
bins = bins.tolist()
df['Profitable Trade Ratio Bin Score'] = pd.cut(x=df['Profitable Trade Ratio'], bins=bins, labels=False)
df['Profitable Trade Ratio Bin Score'] = df['Profitable Trade Ratio Bin Score'].fillna(0)

df.head(10)

[ 5.48396702  5.65175218  6.32278974  7.67773706  7.87127806  8.01637655
  8.29713697  8.35524508  8.38269583  9.62940907 10.87631699 10.90357306
 11.47463353 11.64567109 11.6908841  11.74232707 11.77462208 11.83921209]
[42. 47. 53. 63.]
[2.19942   2.31984   2.3957248 2.5907524 2.6714792 2.94575   3.00109
 3.1443    3.1817472 3.21117   3.235688  3.3100136 5.0675168 5.1385028
 5.174294  5.2214292 5.2887844 5.29257   5.307408  5.319992  5.3433092
 5.4069204 5.45397   5.5206372 5.55594  ]
[0.50794   0.5080232 0.5082    0.5090544 0.50943   0.5097556 0.51163
 0.515278  0.51923   0.5212452 0.52381  ]


Ticker   Parameters Profit (in %) Wouldve Made (in %)  \
25936    NAK    5 28 9 12       207.04%             -43.66%   
26144    NAK   5 32 11 13       321.13%             -43.66%   
26207    NAK   5 33 11 13       321.13%             -43.66%   
27115    NAK    6 30 7 12       195.77%             -43.66%   
27206    NAK   6 31 10 13       300.00%             -43.66%   
27449    NAK    6 35 9 13       291.55%             -43.66%   
28177    NAK    7 30 6 12       195.77%             -43.66%   
30184    NAK    9 28 5 12       207.04%             -43.66%   
30635    NAK    9 35 6 13       291.55%             -43.66%   
31058    NAK  10 42 11 13       464.79%             -43.66%   

       Profitable Trade Ratio Avg Return  Avg Without Best  # of Trades  \
25936                 0.50820    4.71436           2.59710         61.0   
26144                 0.50943    8.30827           3.21117         53.0   
26207                 0.50943    8.30827           3.21117         53.0   
27115                 0.50794    4.43859           2.31984         63.0   
27206                 0.51923    8.34200           3.14430         52.0   
27449                 0.50943    8.10612           3.00109         53.0   
28177                 0.50794    4.43859           2.31984         63.0   
30184                 0.50820    4.71436           2.59710         61.0   
30635                 0.50943    8.10612           3.00109         53.0   
31058                 0.51163   16.78369           5.12273         43.0   

       Bought Price  Profit  Wouldve Made  Outperform Ratio  \
25936           0.0  207.04        -43.66          5.742098   
26144           0.0  321.13        -43.66          8.355245   
26207           0.0  321.13        -43.66          8.355245   
27115           0.0  195.77        -43.66          5.483967   
27206           0.0  300.00        -43.66          7.871278   
27449           0.0  291.55        -43.66          7.677737   
28177           0.0  195.77        -43.66          5.483967   
30184           0.0  207.04        -43.66          5.742098   
30635           0.0  291.55        -43.66          7.677737   
31058           0.0  464.79        -43.66         11.645671   

       Outperform Bin Score  # Trades Bin Score  Avg w/o Best Bin Score  \
25936                   1.0                18.0                     3.0   
26144                   6.0                12.0                     8.0   
26207                   6.0                12.0                     8.0   
27115                   0.0                18.0                     0.0   
27206                   3.0                12.0                     6.0   
27449                   2.0                12.0                     5.0   
28177                   0.0                18.0                     0.0   
30184                   1.0                18.0                     3.0   
30635                   2.0                12.0                     5.0   
31058                  10.0                 6.0                    12.0   

       Profitable Trade Ratio Bin Score  
25936                               1.0  
26144                               3.0  
26207                               3.0  
27115                               0.0  
27206                               7.0  
27449                               3.0  
28177                               0.0  
30184                               1.0  
30635                               3.0  
31058                               5.0

In [12]:
df['Total Score'] = ((df['Outperform Bin Score'] + df['# Trades Bin Score'] + df['Avg w/o Best Bin Score'] + df['Profitable Trade Ratio Bin Score']))
df['Total Score Adj'] = df.apply(lambda x : math.sqrt(x['Total Score'])*10 if (x['Total Score'] > 0) else x['Total Score'], axis = 1)
df['Rough Score'] = (df['# of Trades'] * pd.to_numeric(df['Profitable Trade Ratio'],errors='coerce')) + 7*pd.to_numeric(df['Outperform Ratio'],errors='coerce')

# df = df.drop(columns=['Profit', 'Wouldve Made', 'Avg Without Best','Profitable Trade Ratio','Outperform Ratio'])
df = df.sort_values(by=['Rough Score'], ascending = False)
df.head(10)


Ticker   Parameters Profit (in %) Wouldve Made (in %)  \
34253    NAK   13 41 9 13       473.24%             -43.66%   
33191    NAK  12 41 10 13       470.42%             -43.66%   
33137    NAK  11 41 11 13       470.42%             -43.66%   
33074    NAK  11 40 11 13       469.01%             -43.66%   
34199    NAK  12 40 10 13       469.01%             -43.66%   
34082    NAK  12 39 11 13       469.01%             -43.66%   
33893    NAK  12 36 11 13       467.61%             -43.66%   
33011    NAK  11 39 11 13       466.20%             -43.66%   
34019    NAK  12 38 11 13       464.79%             -43.66%   
31058    NAK  10 42 11 13       464.79%             -43.66%   

       Profitable Trade Ratio Avg Return  Avg Without Best  # of Trades  \
34253                 0.52381   17.47017           5.55201         42.0   
33191                 0.52381   17.37679           5.45397         42.0   
33137                 0.52381   17.37679           5.45397         42.0   
33074                 0.51163   16.94563           5.29257         43.0   
34199                 0.51163   16.94563           5.29257         43.0   
34082                 0.52381   17.47391           5.55594         42.0   
33893                 0.52381   17.33012           5.40496         42.0   
33011                 0.51163   16.86943           5.21265         43.0   
34019                 0.51163   16.81502           5.15559         43.0   
31058                 0.51163   16.78369           5.12273         43.0   

       Bought Price  Profit  Wouldve Made  Outperform Ratio  \
34253           0.0  473.24        -43.66         11.839212   
33191           0.0  470.42        -43.66         11.774622   
33137           0.0  470.42        -43.66         11.774622   
33074           0.0  469.01        -43.66         11.742327   
34199           0.0  469.01        -43.66         11.742327   
34082           0.0  469.01        -43.66         11.742327   
33893           0.0  467.61        -43.66         11.710261   
33011           0.0  466.20        -43.66         11.677966   
34019           0.0  464.79        -43.66         11.645671   
31058           0.0  464.79        -43.66         11.645671   

       Outperform Bin Score  # Trades Bin Score  Avg w/o Best Bin Score  \
34253                  10.0                 6.0                    23.0   
33191                  10.0                 6.0                    21.0   
33137                  10.0                 6.0                    21.0   
33074                  10.0                 6.0                    16.0   
34199                  10.0                 6.0                    16.0   
34082                  10.0                 6.0                    23.0   
33893                  10.0                 6.0                    20.0   
33011                  10.0                 6.0                    14.0   
34019                  10.0                 6.0                    13.0   
31058                  10.0                 6.0                    12.0   

       Profitable Trade Ratio Bin Score  Total Score  Total Score Adj  \
34253                               9.0         48.0        69.282032   
33191                               9.0         46.0        67.823300   
33137                               9.0         46.0        67.823300   
33074                               5.0         37.0        60.827625   
34199                               5.0         37.0        60.827625   
34082                               9.0         48.0        69.282032   
33893                               9.0         45.0        67.082039   
33011                               5.0         35.0        59.160798   
34019                               5.0         34.0        58.309519   
31058                               5.0         33.0        57.445626   

       Rough Score  
34253   104.874505  
33191   104.422375  
33137   104.422375  
33074   104.196380  
34199   104.196380  
34082   104.196310  
33893   103.971

In [13]:
options = {}
options['strings_to_formulas'] = False
options['strings_to_urls'] = False
ticker_list = df['Ticker'].astype(str).unique()
print(ticker_list)


['NAK']


In [14]:
directory =r'C:\Users\amoog\Desktop\crypto_trader\spreadsheets\Backtests'
counters = []
counters.append('0')

for filename in os.listdir(directory):
    f = os.path.join(directory, filename)
    # checking if it is a file
    if os.path.isfile(f):
        num = f.split("\\")[-1].split(' ')[0][-1]
        prev_char = f.split("\\")[-1].split(' ')[0][-2:-1]
        if prev_char != 't':
            counters.append(f.split("\\")[-1].split(' ')[0][-2:])
        else:
            counters.append(num)

counters = list(map(int, counters))
next_num = str(int(max(counters)) + 1)
print(next_num)


38


In [15]:
iterator = 0
firsttime = True

for i in ticker_list:
    df1 = df[df["Ticker"] == ticker_list[iterator]]
    print(ticker_list[iterator])
    display(df1.head(30))
#     try:
    if (firsttime):
        df1.head(25).to_excel( r'C:\Users\amoog\Desktop\crypto_trader\spreadsheets\Backtests\{fOptimizedDate}.xlsx'.format(fOptimizedDate = 'Livetest' + next_num+ ' ' + datetime.now().strftime("%m-%d")), sheet_name = ticker_list[iterator],index=True)
        firsttime=False
    else:
        with pd.ExcelWriter(r'C:\Users\amoog\Desktop\crypto_trader\spreadsheets\Backtests\{fOptimizedDate}.xlsx'.format(fOptimizedDate = 'Livetest' + next_num + ' ' + datetime.now().strftime("%m-%d")), engine='openpyxl',options=options) as writer:
            writer.book = load_workbook(r'C:\Users\amoog\Desktop\crypto_trader\spreadsheets\Backtests\{fOptimizedDate}.xlsx'.format(fOptimizedDate = 'Livetest' + next_num + ' ' + datetime.now().strftime("%m-%d")))
            df1.head(25).to_excel(writer, ticker_list[iterator])
            writer.save()
#     except Exception as e:
#         df1.to_excel( r'C:\Users\amoog\Desktop\crypto_trader\spreadsheets\{fOptimizedDate}.xlsx'.format(fOptimizedDate = 'Livetest ' + datetime.now().strftime("%m-%d")), sheet_name = ticker_list[iterator],index=True)

    iterator+=1
    

NAK


Ticker   Parameters Profit (in %) Wouldve Made (in %)  \
34253    NAK   13 41 9 13       473.24%             -43.66%   
33191    NAK  12 41 10 13       470.42%             -43.66%   
33137    NAK  11 41 11 13       470.42%             -43.66%   
33074    NAK  11 40 11 13       469.01%             -43.66%   
34199    NAK  12 40 10 13       469.01%             -43.66%   
34082    NAK  12 39 11 13       469.01%             -43.66%   
33893    NAK  12 36 11 13       467.61%             -43.66%   
33011    NAK  11 39 11 13       466.20%             -43.66%   
34019    NAK  12 38 11 13       464.79%             -43.66%   
31058    NAK  10 42 11 13       464.79%             -43.66%   
33956    NAK  12 37 11 13       464.79%             -43.66%   
34136    NAK  12 39 10 13       461.97%             -43.66%   
32129    NAK  11 42 11 13       453.52%             -43.66%   
34208    NAK  12 41 11 13       432.39%             -43.66%   
34145    NAK  12 40 11 13       432.39%             -43.66%   
34262    NAK  13 41 10 13       430.99%             -43.66%   
33200    NAK  12 42 11 13       426.76%             -43.66%   
33524    NAK   12 30 5 13       322.54%             -43.66%   
32642    NAK   11 33 5 13       321.13%             -43.66%   
32579    NAK   11 32 5 13       321.13%             -43.66%   
26144    NAK   5 32 11 13       321.13%             -43.66%   
26207    NAK   5 33 11 13       321.13%             -43.66%   
33587    NAK   12 31 5 13       326.76%             -43.66%   
33461    NAK   12 29 5 13       319.72%             -43.66%   
33586    NAK   12 31 5 12       308.45%             -43.66%   
33398    NAK   12 28 5 13       305.63%             -43.66%   
27206    NAK   6 31 10 13       300.00%             -43.66%   
31454    NAK   10 31 6 13       300.00%             -43.66%   
27449    NAK    6 35 9 13       291.55%             -43.66%   
30635    NAK    9 35 6 13       291.55%             -43.66%   

       Profitable Trade Ratio Avg Return  Avg Without Best  # of Trades  \
34253                 0.52381   17.47017           5.55201         42.0   
33191                 0.52381   17.37679           5.45397         42.0   
33137                 0.52381   17.37679           5.45397         42.0   
33074                 0.51163   16.94563           5.29257         43.0   
34199                 0.51163   16.94563           5.29257         43.0   
34082                 0.52381   17.47391           5.55594         42.0   
33893                 0.52381   17.33012           5.40496         42.0   
33011                 0.51163   16.86943           5.21265         43.0   
34019                 0.51163   16.81502           5.15559         43.0   
31058                 0.51163   16.78369           5.12273         43.0   
33956                 0.52381   17.23675           5.30692         42.0   
34136                 0.51163   16.72101           5.05700         43.0   
32129                 0.52381   17.11489           5.17897         42.0   
34208                 0.52381   16.56472           5.33045         42.0   
34145                 0.52381   16.58172           5.34831         42.0   
34262                 0.52381   16.52220           5.28581         42.0   
33200                 0.52381   16.54811           5.31302         42.0   
33524                 0.51923    8.51080           3.31986         52.0   
32642                 0.50943    8.30827           3.21117         53.0   
32579                 0.50943    8.30827           3.21117         53.0   
26144                 0.50943    8.30827           3.21117         53.0   
26207                 0.50943    8.30827           3.21117         53.0   
33587                 0.50980    9.93133           2.43841         51.0   
33461                 0.51923    8.45163           3.25832         52.0   
33586                 0.50909    9.37782           2.19942         55.0   
33398                 0.50943    7.97299           2.86274         53.0   
27206                 0.519

### now = datetime.now()
if (now.hour == 20) and (now.minute == 42):
    print ('hello')
else:
    print (now.hour)
    print (now.minute)